# Experimenting with least squares and its variants

In [1]:
%matplotlib inline

from sklearn import datasets
from scipy.optimize import fmin_bfgs
import numpy as np
from numpy.linalg import norm
from numpy.linalg import inv
from numpy import transpose, identity
from numpy import zeros

## Data preparation

In [2]:
boston = datasets.load_boston()
data = np.array(boston.data)

The boston dataset is one of the standard regression problems used to experiment with learning algorithms. Below you can find the dataset description

In [3]:
print(boston.DESCR)

.. _boston_dataset:

Boston house prices dataset
---------------------------

**Data Set Characteristics:**  

    :Number of Instances: 506 

    :Number of Attributes: 13 numeric/categorical predictive. Median Value (attribute 14) is usually the target.

    :Attribute Information (in order):
        - CRIM     per capita crime rate by town
        - ZN       proportion of residential land zoned for lots over 25,000 sq.ft.
        - INDUS    proportion of non-retail business acres per town
        - CHAS     Charles River dummy variable (= 1 if tract bounds river; 0 otherwise)
        - NOX      nitric oxides concentration (parts per 10 million)
        - RM       average number of rooms per dwelling
        - AGE      proportion of owner-occupied units built prior to 1940
        - DIS      weighted distances to five Boston employment centres
        - RAD      index of accessibility to radial highways
        - TAX      full-value property-tax rate per $10,000
        - PTRATIO  pu

First step to apply the formulae we learnt during the lectures is to rewrite the dataset in homogeneous coordinates (i.e., we append a column of 1 to the matrix containing the examples):

In [4]:
t = np.ones(len(data)).reshape(len(data),1)
data = np.append(data, t, 1)
target = np.array(boston.target)

We now divide the data into a training set $X$ and a test set $X_\textrm{test}$.

In [5]:
X,y = data[0:400,:], target[0:400]
X_test, y_test = data[400:,:], target[400:]

# Exercise

1. Calculate the least square solution (to the regression problem outlined above) and evaluate its performances on the training set and on the test set.
1. Calculate the ridge regression solution (set lambda to 0.01) and evaluate its performances on the training set and on test set.
1. Calculate the lasso regression solution and evaluate its performances on the training set and on the test set.

## Notes

- Here it follows a list of functions you may want to use (the required packages are already imported at the beginning of this notebook) along with a very brief explanation of their purpose (`help(nomefun)` will provide you more information about function `nomefun`):
    - `transpose`: matrix transposition (e.g., `transpose(X)`)
    - `dot`: matrix multiplication (e.g., `X.dot(X2)`) 
    - `inv`: matrix inversion (e.g., `inv(X)`)
- to solve the lasso problem you will need to perform a numerical minimization of the associated loss function (as you know, a closed form solution does not exist). There are many numerical optimization algorithms available in the scipy package. My suggestion is to use `fmin_bfgs`. Here it follows an example of how to use it:
    ```python
        def f(w):
            return w[0]**2 + w[1]**2 + w[0] + w[1]
        
        w = fmin_bfgs(f, [0,0])
    ```
    note that the function may (and should) reference your data variables (i.e., $X$ and $y$).
- to evaluate the performances of your solutions use the $S$ statistic:
    $$
        S =  \sqrt{ \frac{1}{n} \sum_{i=1}^n (y_i' - y_i)^2 }
    $$
    where $y'_i$ is your model prediction for the i-th example, and $n$ is the number of examples.

least squares: $(X^T X)^{-1}X^T y $

In [6]:
least_squares = lambda x,y: inv(x.T.dot(x)).dot(x.T.dot(y))

In [7]:
least_squares(X, y)

array([-1.91246374e-01,  4.42289967e-02,  5.52207977e-02,  1.71631351e+00,
       -1.49957220e+01,  4.88773025e+00,  2.60921031e-03, -1.29480799e+00,
        4.84787214e-01, -1.54006673e-02, -8.08795026e-01, -1.29230427e-03,
       -5.17953791e-01,  2.86725996e+01])

Ridge regression: ŵ  = (XᵀX + λI)⁻¹Xᵀy

In [8]:
def ridge_regression(x, y, lmb):
    I = identity(len(X[0]))
    return inv(x.T.dot(x) + lmb * I).dot(x.T).dot(y)

In [9]:
ridge_regression(X, y, 0.1)

array([-1.92905668e-01,  4.45989360e-02,  4.80153773e-02,  1.70985336e+00,
       -1.21920175e+01,  5.08501051e+00,  8.60369052e-04, -1.23267578e+00,
        4.67418151e-01, -1.51800832e-02, -7.48061272e-01,  7.58288257e-04,
       -5.09848508e-01,  2.39216289e+01])

Lasso: w* = argmin_w (y-X·w)ᵀ(y-X·w) + λ‖w‖₁

In [10]:
def lasso(w, x, y, lmb):
    return (y - x.dot(w)).T.dot(y-x.dot(w)) + lmb * sum(w)
lasso_regression = lambda x, y, lmb: fmin_bfgs(lasso, zeros(len(x[0])), args= (x,y,lmb))

In [11]:
lasso_regression(X,y,0.1)

         Current function value: 8923.891671
         Iterations: 18
         Function evaluations: 1047
         Gradient evaluations: 69


array([-1.91323083e-01,  4.42279444e-02,  5.53631382e-02,  1.71490995e+00,
       -1.50058027e+01,  4.89083693e+00,  2.62969748e-03, -1.29453598e+00,
        4.84604103e-01, -1.53869118e-02, -8.08349218e-01, -1.26958995e-03,
       -5.17749228e-01,  2.86320548e+01])

In [12]:
def S(actual, predicted):
    from math import sqrt
    return sqrt(sum((predicted[i] - actual[i])**2 for i in range(len(actual))) / len(actual))
predicted = lambda x, w: x.dot(w)

In [21]:
w_least = least_squares(X, y)
w_ridge = ridge_regression(X, y, 0.01)
w_ridge = ridge_regression(X, y, 0.2)
w_lasso = lasso_regression(X, y, 0.01)
print("Least squares training set s statistics:", S(y, predicted(X, w_least)))
print("Least squares test set s statistics:", S(y_test, predicted(X_test, w_least)))
print("Ridge regression training set s statistics:", S(y, predicted(X, w_ridge)))
print("Ridge regression test set s statistics:", S(y_test, predicted(X_test, w_ridge)))
print("Lasso regression training set s statistics:", S(y, predicted(X, w_lasso)))
print("Lasso regression test set s statistics:", S(y_test, predicted(X_test, w_lasso)))

         Current function value: 8922.270593
         Iterations: 18
         Function evaluations: 555
         Gradient evaluations: 37
Least squares training set s statistics: 4.722840838326382
Least squares test set s statistics: 6.155792280412581
Ridge regression training set s statistics: 4.734160907532518
Ridge regression test set s statistics: 5.98737876633626
Lasso regression training set s statistics: 4.722840845344215
Lasso regression test set s statistics: 6.155671334655423
